In [91]:
import pandas as pd
import numpy as np
import json
from gensim.models import Word2Vec
import nltk
from nltk.corpus import stopwords
from operator import itemgetter

In [12]:
stop_words = set(stopwords.words('english')) 
stop_words.add('/')
stop_words.add('&')

In [31]:
print(stop_words)

{'as', 'why', 'are', 'they', 'so', 'down', 'about', 'doesn', 'do', 'same', 'itself', 'him', 'ma', 'did', 'me', 'hasn', "won't", 'should', 'its', 'all', 'while', 'then', 'from', 'doing', 't', 'myself', 'through', 'against', 'no', 'that', 'here', 'does', 'her', 'each', 'can', 'not', 'such', 'other', 'himself', 'there', '/', 'above', 'but', 'or', 'out', 'and', 'we', 'haven', "you're", "weren't", 'own', 'my', 'than', 'into', 'now', 'don', "don't", 'wasn', "wasn't", 'any', 'herself', 'until', 'nor', 'll', "haven't", 'was', "shan't", "hasn't", 'these', 'am', 're', 'theirs', "you'll", 'by', 'will', 'ours', 'needn', 'just', 'during', 'to', 'few', 'wouldn', 'only', "wouldn't", 'our', "should've", "you've", "doesn't", 'ourselves', 'yours', 'you', 'some', 'who', 'yourself', 'yourselves', 'once', "shouldn't", 'having', 'the', 'this', 'being', "didn't", "mightn't", 'how', 'a', 'under', 'mustn', 'their', "you'd", 'further', 'had', "hadn't", 'if', 'again', 'on', 'at', 'his', "couldn't", "she's", 'wit

In [19]:
df = pd.read_csv('jobtitles.csv',sep=",", encoding = "ISO-8859-1")

In [20]:
df.sample(5)

Country Code                               Job Title
70020           IN      3+ years of experience in it field
63325           IN                    manager ( contracts)
35603           IN            decision scientist - trainee
64959           IN  association with colleges/universities
45619           IN  associate director - operation manager

In [23]:
dept ={}
with open('departments.json') as json_file:  
    data = json.load(json_file)
    for idx,i in enumerate(data):
        for key, value in i.items():
            dept[key] = value

for key, value in dept.items():
    print(value)
        

['Defence', 'Space', 'Military']
['Animation', 'Entertainment', 'Motion Pictures and Film', 'Computer Games', 'Performing Arts', 'Music', 'Movies', 'Film', 'Actor', 'Actress', 'Audio', 'Video', 'Editor']
['Broadcast Media', 'Media Production', 'Online Publishing', 'Publishing', 'Writing and Editing', 'Newspapers', 'Editing', 'Reporter', 'Journalism', 'Writer']
['Aviation & Aerospace', 'Airlines / Aviation', 'Flight', 'Flight Crew', 'Pilot', 'Steward', 'Marine', 'Shipping', 'Container', 'Air Hostess']
['Medical Practice', 'Mental Health Care', 'Hospital & Health Care', 'Veterinary', 'Medical Device', 'Doctor', 'Nurse', 'Alternative Medicine', 'Pharmaceuticals', 'Biotechnology', 'Nutrition', 'Psychologist', 'Oncology', 'Disease', 'Blood', 'Pharmacy', 'Clinical', 'Cardiovascular', 'Pulmonary']
['Mechanical', 'Automotive', 'Industrial', 'Railroad', 'Shipbuilding', 'Industrial Automation', 'boiler', 'Machinery', 'heavy equipment', 'mechanic', 'assembler']
['Design', 'Graphic Design', 'web D

In [24]:
import gensim
model = gensim.models.KeyedVectors.load_word2vec_format('GoogleNews-vectors-negative300.bin',binary=True)

In [69]:
vec_dict= {}
for key, value in dept.items():
    ll = []
    vec_list=[]
    
    for vals in value:
        words = vals.split(" ")
        #print(words)
        words = list(filter(lambda x: x not in stop_words , words))
        for word in words:
            ll.append(word.lower())
        #map(lambda x:ll.append(x.lower()), words)
        
    print(ll)
    for element in ll:
        try:
            #vec_element = model[element]
            vec_list.append(element)
        except:
            pass
    vec_dict[key] = vec_list

['defence', 'space', 'military']
['animation', 'entertainment', 'motion', 'pictures', 'film', 'computer', 'games', 'performing', 'arts', 'music', 'movies', 'film', 'actor', 'actress', 'audio', 'video', 'editor']
['broadcast', 'media', 'media', 'production', 'online', 'publishing', 'publishing', 'writing', 'editing', 'newspapers', 'editing', 'reporter', 'journalism', 'writer']
['aviation', 'aerospace', 'airlines', 'aviation', 'flight', 'flight', 'crew', 'pilot', 'steward', 'marine', 'shipping', 'container', 'air', 'hostess']
['medical', 'practice', 'mental', 'health', 'care', 'hospital', 'health', 'care', 'veterinary', 'medical', 'device', 'doctor', 'nurse', 'alternative', 'medicine', 'pharmaceuticals', 'biotechnology', 'nutrition', 'psychologist', 'oncology', 'disease', 'blood', 'pharmacy', 'clinical', 'cardiovascular', 'pulmonary']
['mechanical', 'automotive', 'industrial', 'railroad', 'shipbuilding', 'industrial', 'automation', 'boiler', 'machinery', 'heavy', 'equipment', 'mechanic',

In [73]:
vec_dict['Agriculture']

['farming', 'fishery', 'forest', '', 'dairy', 'biologist']

In [116]:
for row in df['Job Title']:
    words = row.split(" ")
    words = list(filter(lambda x: x not in stop_words , words))
    scores_allwords=[]
    for word in words:
        #find distance from each category
        score_dict = {}
        
        for key, value in vec_dict.items():
            #print(key)
            lst=[]
            for val in value:
                #model.similarity(word, val)
                try:
                    #print(word," , ",val," , ",model.similarity(word, val))
                    lst.append(abs(model.similarity(word.lower(), val)))
                except:
                    pass
            #print(np.mean(np.array(lst)))
            score_dict[key]=np.mean(np.array(lst))
        score_dict = sorted(score_dict.items(), key=itemgetter(1))
        #print("score_dict >> ", score_dict)
        scores_allwords.append(score_dict)
    #print(scores_allwords)
    allwords_dict={}
    for x in scores_allwords:
        for key,value in x:
            allwords_dict[key]=allwords_dict.get(key,0)+value
    try:
        print(row," , ",sorted(allwords_dict.items(), key=itemgetter(1),reverse=True)[0:2])
    except:
        print(row," not found")

senior manager operations  ,  ('Management', 0.8777966254177113)
sr.analyst  ,  ('Defense', nan)
test analyst  ,  ('planning and quality', 0.2826118696314317)
system admin  ,  ('Information Technology', 0.4228681897058968)
network administrator  ,  ('Management', 0.43606734882366277)
drama teacher  ,  ('Education', 0.38359591889773265)
software engineer  ,  ('Engineering and Telecommunications', 0.6781237005170544)
so  not found
manager  ,  ('Management', 0.46287877631467395)
am ops  ,  ('Defense', 0.1553925196771296)
quality assurance  ,  ('planning and quality', 0.4837949950539297)
operations marketing manager  ,  ('Marketing and Advertising', 0.9844636402318764)
consultant  ,  ('Management', 0.2891114201161763)
finance & accounts lead  ,  ('Financials', 0.5964180242752303)
manager - mechanical maintenance(civil construction / automobile)  ,  

/Users/anjalisinha/anaconda3/lib/python3.6/site-packages/numpy/core/fromnumeric.py:2920: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/Users/anjalisinha/anaconda3/lib/python3.6/site-packages/numpy/core/_methods.py:85: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


('Chemicals', nan)
working as a asst. planning manager  ,  ('Management', 0.929930108399543)
manufacturing engineer  ,  ('Engineering and Telecommunications', 0.5865476209468834)
design engineer  ,  ('Design', 0.9297379827145296)
claims officer  ,  ('Management', 0.34650541890851616)
associate director,business development,mid corporate group,ratings at crisil ltd  ,  ('Defense', nan)
lead  ,  ('Energy and Mining', 0.09041751172003681)
unit manager  ,  ('Management', 0.6130417682807272)
material planner  ,  ('Design', 0.34819406813376574)
sr.officer  ,  ('Defense', nan)
hr recruiter  ,  ('Human Resources', 0.33289063731160534)
network engineer  ,  ('Engineering and Telecommunications', 0.6419392890682376)
spinning  ,  ('Art and Photography', 0.1281838630361984)
research manager  ,  ('Management', 0.5849127035651763)
partner tech. specialist  ,  ('Chemicals', nan)
additional general manager  ,  ('Management', 0.8076267423999062)
assistant consultant  ,  ('Management', 0.6288666097992442

technical support  ,  ('Design', 0.3544598308894279)
admn  ,  ('Government and Agencies', 0.224742197492737)
business development manager  ,  ('Management', 0.853558314744606)
erp-edp senior team member  ,  ('Defense', nan)
programmer analyst  ,  ('Management', 0.39130697515012175)
general manager projects  ,  ('Management', 0.8797913969806307)
sercvice  ,  ('Defense', nan)
p.a  ,  ('Defense', nan)
back office support  ,  ('Defense', 0.38987858149672494)
head of it, team leader  ,  ('Chemicals', nan)
manager-rf planning & optimization-wireless engineering  ,  ('Defense', nan)
deputy manager  ,  ('Management', 0.7084670871274006)
admin officer  ,  ('Management', 0.3790003146764296)
risk manager  ,  ('Management', 0.5242170500254454)
architect  ,  ('Design', 0.31809270652509347)
sr. design engineer -piping stress  ,  ('Design', nan)
software testing  ,  ('Information Technology', 0.47173080566049075)
graduate test engineer  ,  ('Engineering and Telecommunications', 0.571709678912162)
sen

purchase executive  ,  ('Management', 0.45684028792964204)
assistant manager - risk assurance services  ,  ('Chemicals', nan)
officer opration  ,  ('Design', nan)
lab chemist  ,  ('Chemicals', 0.4409320989901765)
office manager - india operations  ,  ('Design', nan)
assistant manager - design  ,  ('Chemicals', nan)
project engineer (plumbing)  ,  ('Clothing,Cosmetics and Fashion', nan)
sqa engineer  ,  ('Defense', nan)
structural engineer  ,  ('Engineering and Telecommunications', 0.5369121549932803)
town project leader  ,  ('Management', 0.43434252476797025)
financial analyst  ,  ('Financials', 0.49719624570085913)
asst manager finance  ,  ('Management', 0.8213746479909398)
leather agent india  ,  ('Clothing,Cosmetics and Fashion', 0.46134756593299553)
assistant engineer electrical  ,  ('Electrical and Electronics', 0.7779048474584068)
nnn  ,  ('Business Services', 0.07425944762794033)
assistant general manager  ,  ('Management', 1.0672688843275757)
asst. brand manager  ,  ('Managemen

...

senior manager - financial & investor strategy  ,  ('Chemicals', nan)
executive housekeeping  ,  ('Management', 0.48293378057898206)
corporate quality manager  ,  ('Management', 0.7049094068886188)
deputy manager - hr & administration  ,  ('Design', nan)
seniorr software engineer  ,  ('Defense', nan)
management faculty, hrm,  ,  ('Chemicals', nan)
engineer quality power transformer divisoin  ,  ('Social Organisations and NGO', nan)
bv  ,  ('Design', 0.12374793862350111)
sales service manager  ,  ('Marketing and Advertising', 0.8378241441230517)
mining foreman  ,  ('Energy and Mining', 0.5630288763707378)
ta & ps to md  ,  ('Social Organisations and NGO', 0.2667894970264421)
account group head  ,  ('Management', 0.5572843975076875)
dy.general manager-e & m  ,  ('Defense', nan)
senior reasearch analyst  ,  ('Education', 0.432979986124459)
senior associate (project lead)  ,  ('Chemicals', nan)
articled assistant | assurance  ,  ('Defense', nan)
sr. manager- international business  ,  ('De

plant head quality  ,  ('Management', 0.4316883786830622)
srivastav  ,  ('Defense', nan)
sr mechanical/qa/qc engineer  ,  ('sports ,fitness ,leisure and Travel', nan)
head - fabrication  ,  ('Chemicals', nan)
sr. marriage coucellor  ,  ('Design', nan)
i t executive  ,  ('Management', 0.3556898647890771)
founder president  ,  ('Management', 0.469216562619568)
graphic designer,  ,  ('Energy and Mining', nan)
representative india  ,  ('Management', 0.31497522662214567)
avp - investment products, wealth management  ,  ('Defense', nan)
hod hr  ,  ('Mechanical & Heavy Industry', 0.2811054948258184)
wellness consultant  ,  ('sports ,fitness ,leisure and Travel', 0.46299415136627015)
director - hr service delivery | japa  ,  ('Chemicals', nan)
asst. manager (accounts)  ,  ('Trade', nan)
head-film and animation  ,  ('Defense', nan)
technical sales engineer (get)  ,  ('Chemicals', nan)
asst. manager - services and delivery  ,  ('Trade', nan)
manager - trade marketing  ,  ('Chemicals', nan)
amity

unix technical lead  ,  ('Information Technology', 0.45447187203701744)
asst. gen.manager - electronics cell  ,  ('Trade', nan)
director & head corporate finance  ,  ('Management', 0.9733767498211089)
sr. cloud analyst  ,  ('Engineering and Telecommunications', 0.3264987312620682)
sr. systems engineer, datacenter manager  ,  ('Design', nan)
dgm gccd & marketing services  ,  ('Construction', nan)
instrumentation site engineer  ,  ('Design', 0.7626635766305203)
client relationship associate  ,  ('Management', 0.6196111908143977)
dy. manager(projects)  ,  ('Defense', nan)
manager - personnel & admin  ,  ('Chemicals', nan)
sr network designer  ,  ('Design', 0.5893150559329055)
sales manager - star sports  ,  ('Construction', nan)
management traiee  ,  ('Chemicals', nan)
manager- data services practice  ,  ('Defense', nan)
techanical recruiter  ,  ('Defense', nan)
associate director conference & events  ,  ('Management', 0.7974909213490607)
it manager - agile plm practice  ,  ('Chemicals', 

project manager brand solutions  ,  ('Management', 0.8713527516380242)
audit specialist  ,  ('Management', 0.35787654366315785)
product & marketing  ,  ('Marketing and Advertising', 0.8581431047252106)
infosys project manager: acoe, pcoe, testing (transactions, capital markets-equity derivatives)  ,  ('Management', nan)
project manager railway electrification  ,  ('Management', 0.7892521516585744)
deputy general manager - corporate finance  ,  ('Design', nan)
ebgineer  ,  ('Defense', nan)
sr. officer bpo operation  ,  ('Management', 0.5354684789443428)
assistant general manager - hpd  ,  ('Chemicals', nan)
co-founder & creative head/visual effects supervisor  ,  ('Defense', nan)
consultant-engineering and scrummaster/agile:scrum practitioner  ,  ('Defense', nan)
asst. vice president - procurement (bulk chemicals)  ,  ('Trade', nan)
assistant vice president-marketing  ,  ('Chemicals', nan)
scientist engineer  ,  ('Engineering and Telecommunications', 0.5328940530647629)
officer - inform

senior manager business development - marine offshore and ports  ,  ('Chemicals', nan)
portfolio control manager  ,  ('Management', 0.6687204118709926)
maintanance troubleshooter  ,  ('Mechanical & Heavy Industry', 0.37101163862284403)
division manager - it projects  ,  ('Energy and Mining', nan)
professor g, imsc, chennai.  ,  ('Import Export Procurement Dealers and Distributors', nan)
project co-ordinator,pm team  ,  ('Clothing,Cosmetics and Fashion', nan)
technical lead- cyber security & privacy  ,  ('Chemicals', nan)
programme manager, enterprise security solutions  ,  ('Defense', nan)
hcc  ,  ('Defense', nan)
founder, director & chief digital officer  ,  ('Defense', nan)
founder & chief digital officer  ,  ('Management', 0.8200621749735919)
application dev  ,  ('Design', 0.4394896637383059)
ware house stock incharge  ,  ('Trade', 0.5381590135363145)
ctl  ,  ('Defense', nan)
youth wing coordinator  ,  ('Management', 0.43346160718771853)
alcatel ippabx - asst.manager / customer supp

In [80]:
lst

[0.02750924703881209,
 0.11996028997488638,
 0.03693586360721243,
 0.19184762693614807,
 0.07192699464471983,
 0.01018656380840928,
 0.10149364865680136,
 0.21213349264360504,
 -0.023567919060228593]

In [42]:
model["manager"]

array([-1.64062500e-01, -6.17675781e-02, -5.41992188e-02, -3.76953125e-01,
       -1.54296875e-01,  1.12304688e-01,  1.61132812e-01, -2.75390625e-01,
        7.32421875e-02,  8.15429688e-02, -2.21252441e-03,  1.74804688e-01,
       -1.56250000e-01, -3.55468750e-01,  6.49414062e-02,  6.54296875e-02,
        1.50390625e-01, -2.78320312e-02, -1.02539062e-01,  9.52148438e-02,
       -1.52343750e-01,  1.76757812e-01,  5.78613281e-02,  1.20117188e-01,
        3.86718750e-01,  5.15136719e-02, -1.86523438e-01,  2.61718750e-01,
       -2.61718750e-01,  1.25976562e-01, -1.93359375e-01,  2.43164062e-01,
       -6.13403320e-03, -1.08398438e-01,  2.26562500e-01,  1.89208984e-02,
       -6.25000000e-02,  2.25585938e-01,  2.40234375e-01, -2.40478516e-02,
        8.34960938e-02, -3.84765625e-01, -4.02832031e-02, -6.00585938e-02,
       -9.57031250e-02, -2.40234375e-01, -2.96875000e-01,  2.34375000e-01,
       -5.07812500e-02,  2.36328125e-01, -1.14257812e-01,  7.27539062e-02,
       -4.51660156e-02,  

In [61]:
model.similarity('chef', 'cook')

/Users/anjalisinha/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  """Entry point for launching an IPython kernel.


0.5625564131570292

In [63]:
model.similarity('civil', 'landman')

0.08788757780511613

In [64]:
model.similarity('lawyer', 'defense')

0.27856308581334743

In [67]:
model.similarity('crew', 'nurse')

0.17276023209378827